# Скрипт для анализа изображений

## Импорты, константы

In [ ]:
from PIL import Image
import json
import numpy as np
import os
import pandas as pd
import pathlib
import re
from tqdm.notebook import tqdm
import requests

from bs4 import BeautifulSoup
import base64

Имя для сохранения таблички.

In [ ]:
full_name = 'img_list.xlsx'

Задаем токен и номер ветви для проверки.

In [ ]:
github_token = 'Input Your Github Access Token Here'
dev_branch = 'dev-2.0'
#mypath = '/content/'

In [ ]:
pd.set_option('display.max_colwidth', 3000)
pd.set_option('display.max_rows', 100)

## Функции

Функция для получения списка ноутбуков.

In [ ]:
# def get_notebooks_list(local=False):
#     '''
#     function to get list of notebooks paths
#     '''

#     if local:
#         # to store file names
#         res = []

#         # construct path object
#         d = pathlib.Path(mypath)

#         # iterate directory
#         for entry in d.iterdir():
#             # check if it a file
#             if entry.is_file():
#                 res.append(entry)
#         # return only notebooks
#         lecture_names = [i.__str__() for i in res if '.ipynb' in i.__str__()]
#         lecture_names.sort()
#         return lecture_names

#     else:

#         headers = {}
#         if github_token:
#             headers['Authorization'] = f"token {github_token}"

#         url = f'https://api.github.com/repos/EPC-MSU/EduNet-lectures/contents/out/?ref={dev_branch}'
#         r = requests.get(url, headers=headers)
#         r.raise_for_status()
#         data = r.json()

#         lecture_names = [x['name'] for x in data if '.ipynb' in x['name']]

#         return [f'https://api.github.com/repos/EPC-MSU/EduNet-lectures/contents/out/{lecture}?ref={dev_branch}' for lecture in lecture_names]


# res = get_notebooks_list(local=False)
# if mypath is not None:
#    res2 = get_notebooks_list(local=True)
# else: res2 = None
# res #, res2

На текущий момент неактуально для 2.0, поэтому зададим списком:

In [ ]:
lectures = ['L01_Intro.ipynb', 'L02_Linear_models.ipynb', 'L03_Classic_ML.ipynb', 'L04_Feature_Engineering.ipynb', 'L05_Neural_networks.ipynb', 'L06_CNN.ipynb', 'L07_Learning_techniques.ipynb', 'L08_NN_architectures.ipynb', 'L09_RNN.ipynb', 'L10_Transformers.ipynb', 'L11_Segmentation_Detection.ipynb', 'L12_Representation_learning.ipynb', 'L13_Generative_models.ipynb', 'L14_Explainability.ipynb', 'L15_RL.ipynb']

Функция для получения всех содержимых полей маркдаун в одном файле.

In [ ]:
def get_all_text_from_notebook(lecture):
    '''
    function to get only markdown cells from json file
    '''
    url = f'https://api.github.com/repos/EPC-MSU/EduNet-lectures/contents/out/{lecture}?ref={dev_branch}'

    if 'github' in url:

        # github
        headers = {}
        if github_token:
            headers['Authorization'] = f"token {github_token}"
        r = requests.get(url, headers=headers)
        r.raise_for_status()
        data = r.json()
        file_content = data['content']
        file_content_encoding = data.get('encoding')
        if file_content_encoding == 'base64':
            file_content = base64.b64decode(file_content).decode()
        try:
            file_content = json.loads(file_content)
        except Exception as e:
            print('error at', url)
            print(e)
            return ''

    else:

        # local
        try:
            with open("/content/{lecture}", mode="r", encoding="utf-8") as f:
                file_content = json.load(f)
        except Exception as e:
            print('error at', "/content/{lecture}")
            print(e)
            return ''


    # get only text cells and unite them into a single string
    text = ''
    l = [cell for cell in file_content['cells'] if cell['cell_type'] == 'markdown']
    for i, c in enumerate(l):
        text += ' '.join(c['source'])
    return text

full_text = get_all_text_from_notebook(lectures[0])
full_text[:min(1000, len(full_text))] + '...'

Функция для загрузки картинки по ссылке и сохранению ее ширины, высоты и веса в килобайтах.

In [ ]:
def get_size_from_url(url):
    '''
    download file, save, read content, get parameters, delete file
    '''

    # get file extention
    ext = url.split('.')[-1]

    # download file
    img_data = requests.get(url).content
    tmp_name = 'tmp.' + ext

    # save file
    with open(tmp_name,'wb') as handler:
        handler.write(img_data)

    file_stats = os.stat(tmp_name)
    file_size = file_stats.st_size // 1024

    # read file
    try:
        with Image.open(tmp_name) as image:
            params = image.height, image.width, file_size
    except:
        return None, None, None

    # delete file
    os.remove(tmp_name)

    if len(params) ==3:
        return params
    else:
        return None, None, None

test_url = 'https://edunet.kea.su/repo/EduNet-content/L09/out/compare_basic_and_wide_residual_blocks.png'
# test_url = 'https://edunet.kea.su/repo/EduNet-content/L02/out/use_knn_to_comare_imgs_to_find_similar.jpg'
get_size_from_url(test_url)

Функция пробегает по текстовой строке, находит все ссылки на картинки и делает лист из словарей с параметрами картинок.

In [ ]:
def get_urls_and_widths_from_text(full_text):
    '''
    find all images in text and their parameters
    '''

    # regex strings to check
    regex_strings = [
        r'\<.*?img.*?src*.?=(.*?)>',
    #     r'!\[(.*)\]\((.*)\)' - this proved unnecessary
    ]

    images_parameters = []

    for r_str in regex_strings:
        all_matches_img_src = re.findall(r_str, full_text)

        for string in all_matches_img_src:

            image_parameters = {}

            string = re.sub(f'(\d\d\s*?)(px)', r'\1', string) # remove all 'px' from width=

            image_parameters['string'] = string

            image_parameters['url'] = re.findall(r'\"(.*?)\"', string)[0]

            regex_image_params = [
                r'width\D*(\d+)',
                r'height\D*(\d+)',
                r'L(\d*)'
            ]

            dict_names_params = [
                'width_set',
                'height_set',
                'lect_№'
            ]

            for reg, name in zip(regex_image_params, dict_names_params):
                tmp = re.findall(reg, string)
                if len(tmp) > 0:
                    try:
                        tmp = int(tmp[0])
                    except:
                        print('error!!!', string)
                else:
                    tmp = None

                image_parameters[name] = tmp

            try:
                real_size = get_size_from_url(image_parameters['url'])
            except:
                real_size = [None, None]

            image_parameters['width_real'] = real_size[1]
            image_parameters['height_real'] = real_size[0]
            image_parameters['file_size_kb'] = real_size[2]

            images_parameters.append(image_parameters)

    return images_parameters

get_urls_and_widths_from_text(full_text[:min(2000, len(full_text))])

Функция добавляет элементарные расчеты по данным.

In [ ]:
def calculate_scale(dataframe):
    '''
    adds some calculations to dataframe
    '''
    # calculate scaling
    dataframe['scale'] = dataframe['width_real'] / dataframe['width_set']
    dataframe['scale'] = dataframe['scale'].fillna(
        dataframe['height_real'] / dataframe['height_set']
    ).round(4)

    # our content or web-dep
    dataframe['original'] = 1 - dataframe['url'].str.contains('web_dependencies')

    # make data integer (with nans)
    for c in dataframe.columns:
        try:
            dataframe[c] = dataframe[c].astype('Int16')
        except:
            pass

    return dataframe[dataframe.columns[::-1]]

Функция по списку ссылок на ноутбуки ИЛИ их адресов на диске делает датафрейм с параметрами всех картинок.

In [ ]:
def create_images_table(notebooks_list):
    '''
    creates dataframe with all found images and their parameters
    '''

    images_table = []

    # for every file in list...
    for i, l_name in enumerate(tqdm(notebooks_list)):
        # get only text content as a string
        full_text = get_all_text_from_notebook(l_name)
        # get images from the string and append to list
        images_table += get_urls_and_widths_from_text(full_text)

    # create DF and add some calculations
    df = pd.DataFrame(images_table)
    df = calculate_scale(df)
    return df

## Запуск

А вот так оно будет работать на практике

In [ ]:
#lecture_names = get_notebooks_list(local=False)
# lecture_names = get_notebooks_list(local=True)


df = create_images_table(lectures)
df = df.sort_values('lect_№')
df.to_excel(full_name)
print('всего картинок найдено', len(df))
df.head()

Полный датафрейм, если надо

In [ ]:
# df

Можно загрузить заранее сохраненный файл для анализа.

In [ ]:
# df = pd.read_excel(full_name, index_col=0)

## Анализ

### Задана высота картинки при вставке (а надо задавать ширину)

In [ ]:
df[df['height_set'].notna()]

### Размер вставки больше 1024 (в любом случае будет масштабировано до 1024)

In [ ]:
df[df['width_set'] > 1024]

### Нерабочие ссылки

In [ ]:
df[df['file_size_kb'].isna()]

### Неверный масштаб для перерисованных (content) картинок:

In [ ]:
a = df[df['original']==1]
a = a[a['scale'].notna()]
a = a[a['scale'] != 2]
a.sort_values('scale')

### Низкое разрешение чужих картинок

In [ ]:
a = df[df['original']==0]
a = a[a['scale'] < 2].sort_values('scale')
a = a[~a['url'].str.contains('.gif')]
# a = a.groupby('lect_№').count()['scale']
a